In [1]:
import pandas as pd
import pathlib
import geopandas as gpd
import matplotlib.pyplot as plt
import pypsa
import numpy as np
import seaborn as sbn
import cartopy.crs as ccrs
pd.options.display.max_columns = None
pd.options.display.max_rows = None

/opt/anaconda3/envs/pypsa-earth/lib/python3.10/site-packages/pypsa/networkclustering.py:23: UserWarning:

The namespace `pypsa.networkclustering` is deprecated and will be removed in PyPSA v0.24. Please use `pypsa.clustering.spatial instead`. 



# Load the input data

In [2]:
base_path = pathlib.Path("/Users/fabriziofinozzi/Desktop/OpenEnergyTransition/repo/")
base_network_pypsa_earth = pypsa.Network(pathlib.Path(base_path, "geothermal-modelling/workflow/pypsa-earth/networks/US_2021/base.nc"))
base_network_pypsa_usa = pypsa.Network(pathlib.Path(base_path, "pypsa-usa/workflow/resources/Default/usa/elec_base_network.nc"))
eia_base_network = gpd.read_file(pathlib.Path(base_path, "US_Electric_Power_Transmission_Lines_5037807202786552385.geojson"))

/opt/anaconda3/envs/pypsa-earth/lib/python3.10/site-packages/pypsa/components.py:318: FutureWarning:

Setting an item of incompatible dtype is deprecated and will raise an error in a future version of pandas. Value '[]' has dtype incompatible with float64, please explicitly cast to a compatible dtype first.

/opt/anaconda3/envs/pypsa-earth/lib/python3.10/site-packages/pypsa/components.py:318: FutureWarning:

Setting an item of incompatible dtype is deprecated and will raise an error in a future version of pandas. Value '[]' has dtype incompatible with float64, please explicitly cast to a compatible dtype first.

/opt/anaconda3/envs/pypsa-earth/lib/python3.10/site-packages/pypsa/components.py:318: FutureWarning:

Setting an item of incompatible dtype is deprecated and will raise an error in a future version of pandas. Value '[]' has dtype incompatible with float64, please explicitly cast to a compatible dtype first.

/opt/anaconda3/envs/pypsa-earth/lib/python3.10/site-packages/pypsa/com

The total number of lines in the EIA dataset is

In [3]:
eia_base_network["geometry"] = eia_base_network["geometry"].boundary
eia_base_network[["ID", "TYPE", "VOLTAGE", "VOLT_CLASS", "SUB_1", "SUB_2", "SHAPE__Len", "geometry"]].head(2)

ID          TYPE  VOLTAGE VOLT_CLASS          SUB_1        SUB_2  \
0  100511  AC; Overhead    115.0    100-161   Waters River    Tap136228   
1  140809  AC; Overhead    161.0    100-161  Phillips Bend  John Sevier   

     SHAPE__Len                                           geometry  
0     79.523416  MULTIPOINT ((-70.92855 42.54359), (-70.92841 4...  
1  24018.513114  MULTIPOINT ((-82.96123 36.37699), (-82.80788 3...

In [4]:
eia_base_network["geometry"]

0        MULTIPOINT ((-70.92855 42.54359), (-70.92841 4...
1        MULTIPOINT ((-82.96123 36.37699), (-82.80788 3...
2        MULTIPOINT ((-75.33407 43.08946), (-75.34449 4...
3        MULTIPOINT ((-89.93728 30.00905), (-89.89741 3...
4        MULTIPOINT ((-90.56609 41.61256), (-90.52954 4...
5        MULTIPOINT ((-86.83214 33.85509), (-86.81425 3...
6        MULTIPOINT ((-71.02486 42.39487), (-71.00767 4...
7        MULTIPOINT ((-75.33410 43.08902), (-75.63113 4...
8        MULTIPOINT ((-90.53585 41.81095), (-90.29540 4...
9        MULTIPOINT ((-81.78570 41.40842), (-81.78477 4...
10       MULTIPOINT ((-90.06720 31.58948), (-90.13096 3...
11       MULTIPOINT ((-94.48206 39.13330), (-94.47888 3...
12       MULTIPOINT ((-80.59603 34.27358), (-80.59845 3...
13       MULTIPOINT ((-90.24759 32.33969), (-90.24803 3...
14       MULTIPOINT ((-83.13040 38.31209), (-83.12589 3...
15       MULTIPOINT ((-83.55530 41.59428), (-83.61004 4...
16       MULTIPOINT ((-90.17902 36.58693), (-90.17491 3.

At first glance, it is possible to see that some transmission lines correspond to a voltage of -999999.0 kV. In particular the number of lines corresponding to -999999.0 is

In [ ]:
eia_base_network.loc[eia_base_network["VOLTAGE"]==-999999.0].shape[0]

which acoounts for almost 15 % of the lines in the EIA dataset

In [ ]:
eia_base_network.loc[eia_base_network["VOLTAGE"]==-999999.0].shape[0]/eia_base_network.shape[0]*100

For the moment, such lines are filtered out

In [ ]:
eia_base_network = eia_base_network.loc[eia_base_network["VOLTAGE"]!=-999999.0]
eia_base_network.shape[0]

Get the voltage bins from the reference data

In [ ]:
eia_voltage_bins_flags = eia_base_network["VOLT_CLASS"].unique().tolist()
eia_voltage_bins_flags

In [ ]:
volt_class_min_values = []
volt_class_max_values = []
for bin_name in eia_voltage_bins_flags:
    volt_class_min_values.append(eia_base_network.loc[eia_base_network["VOLT_CLASS"]==bin_name]["VOLTAGE"].min())
    volt_class_max_values.append(eia_base_network.loc[eia_base_network["VOLT_CLASS"]==bin_name]["VOLTAGE"].max())
volt_class_bin_limits = pd.DataFrame(
    {
        "voltage_class": eia_voltage_bins_flags,
        "voltage_class_min": volt_class_min_values,
        "voltage_class_max": volt_class_max_values,
    }
)
volt_class_bin_limits

The voltage classes in the EIA dataset include also *Dc*. The number of lines corresponding to such voltage class is

In [ ]:
eia_base_network.loc[eia_base_network["VOLT_CLASS"]=='Dc'].shape[0]

Considering that the PyPSA-Earth base network does not contain any DC line

In [ ]:
base_network_pypsa_earth.lines["dc"].unique()

the lines corresponding to the *Dc* voltage class are removed from the EIA dataset

In [ ]:
eia_base_network = eia_base_network.loc[eia_base_network["VOLT_CLASS"]!='Dc']
eia_base_network.shape[0]

Furthermore, the lines corresponding to the voltage class *Not Available* are removed as well

In [ ]:
eia_base_network = eia_base_network.loc[eia_base_network["VOLT_CLASS"]!='Not Available']
eia_base_network.shape[0]

In [ ]:
eia_base_network["STATUS"].unique()

In [ ]:
base_network_pypsa_earth.lines.shape[0]

# PyPSA-Earth - EIA comparison

Add the voltage class to the PyPSA-Earth base network

In [ ]:
base_network_pypsa_earth.lines["v_nom_class"] = base_network_pypsa_earth.lines["v_nom"]
base_network_pypsa_earth.lines.head(2)

In [ ]:
v_nom_class_dict_pypsa_earth = {
    55.: 'Under 100',
    57.1: 'Under 100', 
    60.: 'Under 100',
    66.: 'Under 100',  
    69.: 'Under 100',  
    70.: 'Under 100',  
    88.: 'Under 100', 
    92.: 'Under 100', 
    100.: "100-161",
    115.: "100-161", 
    120.: "100-161",  
    125.: "100-161",  
    138.: "100-161",  
    160.: "100-161",  
    161.: "100-161",
    220.: "220-287",
    230.: "220-287",
    287.: "220-287",
    345.: "345",
    500.: "500",
    765.: "735 And Above"
}

In [ ]:
base_network_pypsa_earth.lines["v_nom_class"] = base_network_pypsa_earth.lines["v_nom_class"].replace(v_nom_class_dict_pypsa_earth)
base_network_pypsa_earth.lines.head(2)

### Count plot

In [ ]:
sbn.countplot(data=base_network_pypsa_earth.lines, x=base_network_pypsa_earth.lines["v_nom_class"]).set(title='PyPSA-Earth base network')

In [ ]:
sbn.countplot(data=eia_base_network, x=eia_base_network["VOLT_CLASS"], color="orange").set(title='EIA network topology')

### Maps

In [ ]:
# Available voltage classes are:
# Under 100
# 100-161
# 220-287
# 345
# 500
# 735 And Above

selected_voltage_class_earth = "735 And Above"

In [ ]:
base_network_pe_volt_class = base_network_pypsa_earth.lines.loc[base_network_pypsa_earth.lines["v_nom_class"] == selected_voltage_class_earth]
base_network_pe_volt_class = gpd.GeoDataFrame(base_network_pe_volt_class, geometry=gpd.GeoSeries.from_wkt(base_network_pe_volt_class.geometry), crs="EPSG:4326")
base_network_pe_volt_class["union_geo"] = 0
base_network_pe_volt_class = base_network_pe_volt_class.dissolve(by="union_geo")
base_network_pe_volt_class = base_network_pe_volt_class.to_crs(3857)

eia_base_network_volt_class = eia_base_network.loc[eia_base_network["VOLT_CLASS"]==selected_voltage_class_earth]
eia_base_network_volt_class["union_geo"] = 0
eia_base_network_volt_class = eia_base_network_volt_class.dissolve(by="union_geo")
eia_base_network_volt_class = eia_base_network_volt_class.to_crs(3857)

In [ ]:
base_network_pe_volt_class.geometry

In [ ]:
intersection_geometries = base_network_pe_volt_class.intersection(eia_base_network_volt_class)
fig, ax = plt.subplots(figsize=(20, 4))
ax.set_axis_off()

intersection_geometries.plot(ax=ax, color="black", markersize=5)
base_network_pe_volt_class.plot(ax=ax, color="blue", kind="geo")
eia_base_network_volt_class.plot(ax=ax, color="orange", kind="geo")

In [ ]:
!pip install -U kaleido

In [ ]:
import plotly.express as px
import shapely
import kaleido

lats = []
lons = []

for feature in zip(base_network_pe_volt_class.geometry):
    if isinstance(feature, shapely.geometry.linestring.LineString):
        linestrings = [feature]
    elif isinstance(feature, shapely.geometry.multilinestring.MultiLineString):
        linestrings = feature.geoms
    else:
        continue
    for linestring in linestrings:
        x, y = linestring.xy
        lats = np.append(lats, y)
        lons = np.append(lons, x)

fig = px.line_map(lat=lats, lon=lons)
fig.write_image("plotly_test.png")

In [ ]:
fig.savefig("network_comparison_for_voltage_class_{}.png".format(str(selected_voltage_class_earth)))

In [ ]:
eia_base_network_765["union_geo"] = 0
eia_base_network_new = eia_base_network_765.dissolve(by="union_geo")
eia_base_network_new

In [ ]:
base_network_pypsa_earth.lines["line_width"] = 0.0
base_network_pypsa_earth.lines.loc[base_network_pypsa_earth.lines["v_nom_class"] == selected_voltage_class_earth, "line_width"] = 1.0

fig, (ax1, ax2) = plt.subplots(nrows=1, ncols=2, sharey=True, subplot_kw={"projection":ccrs.PlateCarree(), "projection":ccrs.PlateCarree()}, figsize=(20, 4))
base_network_pypsa_earth.plot(line_widths = base_network_pypsa_earth.lines["line_width"], bus_sizes = 0, line_colors = "blue", ax=ax1)
base_network_pypsa_earth.plot(line_widths = base_network_pypsa_earth.lines["line_width"], bus_sizes = 0, line_colors = "white", ax=ax2)
eia_base_network.loc[eia_base_network["VOLT_CLASS"]==selected_voltage_class_earth].plot(ax=ax2, color="orange")
fig.suptitle("Comparison for voltage class: {}".format(selected_voltage_class_earth))
ax1.set_aspect('equal')
ax1.title.set_text("PyPSA-Earth base network")
ax2.set_aspect("equal")
ax2.title.set_text("EIA network")

# PyPSA-USA - EIA comparison

Add the voltage class to the PyPSA-USA base network

In [ ]:
base_network_pypsa_usa.lines["v_nom_class"] = base_network_pypsa_usa.lines["v_nom"]
base_network_pypsa_usa.lines.head(2)

In [ ]:
base_network_pypsa_usa.lines.v_nom.unique()

In [ ]:
v_nom_class_dict_pypsa_usa = {
    69.: 'Under 100',
    100.: "100-161",
    138.: "100-161", 
    115.: "100-161", 
    161.: "100-161",
    230.: "220-287",
    345.: "345",
    500.: "500",
    765.: "735 And Above"
}

In [ ]:
base_network_pypsa_usa.lines["v_nom_class"] = base_network_pypsa_usa.lines["v_nom_class"].replace(v_nom_class_dict_pypsa_usa)

### Maps

In [ ]:
# Available voltage classes are:
# Under 100
# 100-161
# 220-287
# 345
# 500
# 735 And Above

selected_voltage_class_usa = "735 And Above"

In [ ]:
base_network_pypsa_usa.lines["line_width"] = 0.0
base_network_pypsa_usa.lines.loc[base_network_pypsa_usa.lines["v_nom_class"] == selected_voltage_class_usa, "line_width"] = 1.0

fig, (ax1, ax2) = plt.subplots(nrows=1, ncols=2, sharey=True, subplot_kw={"projection":ccrs.PlateCarree(), "projection":ccrs.PlateCarree()}, figsize=(20, 4))
base_network_pypsa_usa.plot(line_widths = base_network_pypsa_usa.lines["line_width"], bus_sizes = 0, line_colors = "blue", ax=ax1)
base_network_pypsa_usa.plot(line_widths = base_network_pypsa_usa.lines["line_width"], bus_sizes = 0, line_colors = "white", ax=ax2)
eia_base_network.loc[eia_base_network["VOLT_CLASS"]==selected_voltage_class_usa].plot(ax=ax2, color="orange")
fig.suptitle("Comparison for voltage class: {}".format(selected_voltage_class_usa))
ax1.set_aspect('equal')
ax1.title.set_text("PyPSA-USA base network")
ax2.set_aspect("equal")
ax2.title.set_text("EIA network")

In [ ]:
fig.savefig("network_comparison_pusa_for_voltage_class_{}.png".format(str(selected_voltage_class_usa)))

## Compare crossings

In [5]:
gadm_usa_json_path_level_1 = "/Users/fabriziofinozzi/Desktop/OpenEnergyTransition/repo/geothermal-modelling/analysis/data/gadm41_USA_1.json"
gadm_gdp_usa_level_1 = gpd.read_file(gadm_usa_json_path_level_1)

In [6]:
gadm_gdp_usa_level_1.head(2)

GID_1 GID_0       COUNTRY   NAME_1  VARNAME_1 NL_NAME_1 TYPE_1 ENGTYPE_1  \
0  USA.1_1   USA  UnitedStates  Alabama    AL|Ala.        NA  State     State   
1  USA.2_1   USA  UnitedStates   Alaska  AK|Alaska        NA  State     State   

  CC_1 HASC_1  ISO_1                                           geometry  
0   NA  US.AL  US-AL  MULTIPOLYGON (((-88.12060 30.23320, -88.12330 ...  
1   NA  US.AK  US-AK  MULTIPOLYGON (((-179.13150 51.20970, -179.1328...

Apply a spatial join between the reference transmission lines topology from EIA and the GADM shapes (level 1)

In [13]:
spatial_join_gadm_eia = eia_base_network.sjoin(gadm_gdp_usa_level_1, how="inner")
spatial_join_gadm_eia.head(2)

OBJECTID_1  OBJECTID      ID          TYPE      STATUS NAICS_CODE  \
0           1         1  100511  AC; Overhead  In Service     221121   
1           2         2  140809  AC; Overhead  In Service     221121   

                                     NAICS_DESC                     SOURCE  \
0  Electric Bulk Power Transmission and Control  Imagery, EIA 861, EIA 860   
1  Electric Bulk Power Transmission and Control           Imagery, EIA 860   

                      SOURCEDATE VAL_METHOD                       VAL_DATE  \
0  Tue, 08 Nov 2016 00:00:00 GMT    Imagery  Mon, 27 Mar 2017 00:00:00 GMT   
1  Wed, 16 Apr 2014 00:00:00 GMT    Imagery  Wed, 15 Feb 2017 00:00:00 GMT   

                OWNER  VOLTAGE VOLT_CLASS INFERRED          SUB_1  \
0       Not Available    115.0    100-161      Yes   Waters River   
1  Kingsport Power Co    161.0    100-161      Yes  Phillips Bend   

         SUB_2    SHAPE__Len                              GlobalID  \
0    Tap136228     79.523416  f1500a3a-804a-4da4-b6f6-bd0fbb2cf36d   
1  John Sevier  24018.513114  58c24e54-d758-4071-9ebf-d83beb60c707   

                                            geometry  index_right     GID_1  \
0  MULTIPOINT ((-70.92855 42.54359), (-70.92841 4...           21  USA.22_1   
1  MULTIPOINT ((-82.96123 36.37699), (-82.80788 3...           42  USA.43_1   

  GID_0       COUNTRY         NAME_1                       VARNAME_1  \
0   USA  UnitedStates  Massachusetts  CommonwealthofMassachusetts|MA   
1   USA  UnitedStates      Tennessee                        TN|Tenn.   

  NL_NAME_1 TYPE_1 ENGTYPE_1 CC_1 HASC_1  ISO_1  
0        NA  State     State   NA  US.MA  US-MA  
1        NA  State     State   NA  US.TN  US-TN

In [14]:
spatial_join_gadm_eia = spatial_join_gadm_eia[["ID", "TYPE", "GID_1", "VOLTAGE", "VOLT_CLASS", "SUB_1", "SUB_2", "ISO_1", "NAME_1", "SHAPE__Len", "geometry"]]

In [15]:
spatial_join_gadm_eia.head(2)

ID          TYPE     GID_1  VOLTAGE VOLT_CLASS          SUB_1  \
0  100511  AC; Overhead  USA.22_1    115.0    100-161   Waters River   
1  140809  AC; Overhead  USA.43_1    161.0    100-161  Phillips Bend   

         SUB_2  ISO_1         NAME_1    SHAPE__Len  \
0    Tap136228  US-MA  Massachusetts     79.523416   
1  John Sevier  US-TN      Tennessee  24018.513114   

                                            geometry  
0  MULTIPOINT ((-70.92855 42.54359), (-70.92841 4...  
1  MULTIPOINT ((-82.96123 36.37699), (-82.80788 3...

In [17]:
spatial_join_gadm_eia["SHAPE__Len"].max()

1781469.77660848

In [18]:
spatial_join_gadm_eia[spatial_join_gadm_eia["SHAPE__Len"]==1781469.77660848]

ID TYPE     GID_1  VOLTAGE VOLT_CLASS   SUB_1        SUB_2  ISO_1  \
69088  200823   DC   USA.5_1   1000.0         Dc  Celilo  Sylmar East  US-CA   
69088  200823   DC  USA.38_1   1000.0         Dc  Celilo  Sylmar East  US-OR   

           NAME_1    SHAPE__Len  \
69088  California  1.781470e+06   
69088      Oregon  1.781470e+06   

                                                geometry  
69088  MULTIPOINT ((-121.11308 45.59461), (-118.48113...  
69088  MULTIPOINT ((-121.11308 45.59461), (-118.48113...

The line above is the longest and it goes from around LA to Oregon.

Apply a spatial join between the transmission lines topology from the PyPSA-Earth base network and the GADM shapes (level 1)

In [ ]:
base_network_pypsa_earth_geopandas = gpd.GeoDataFrame(base_network_pypsa_earth.lines, geometry=gpd.GeoSeries.from_wkt(base_network_pypsa_earth.lines.geometry), crs="EPSG:4326")

In [ ]:
spatial_join_gadm_pypsa_earth = base_network_pypsa_earth_geopandas.sjoin(gadm_gdp_usa_level_1, how="inner")
spatial_join_gadm_pypsa_earth.head(5)

In [ ]:
spatial_join_gadm_pypsa_earth[["GID_1", "v_nom", "v_nom_class", "type", "num_parallel", "ISO_1", "NAME_1"]].head(2)